<a href="https://colab.research.google.com/github/coralie-sorbet/Enhancing-LLM-with-human-feedback/blob/main/Project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Complete RLHF Pipeline with PPO**


# **Load Libraries and configuration of the models**


In [ ]:
# import torch
# import os
# from transformers import AutoTokenizer, AutoModelForCausalLM,  AutoModelForSequenceClassification
# from trl import AutoModelForCausalLMWithValueHead, PPOConfig, PPOTrainer, RewardConfig, RewardTrainer, setup_chat_format, ModelConfig
# from datasets import load_dataset
# from torch.amp import autocast, GradScaler

# # Set model name and device (use GPU if available)
# model_name = "gpt2"  # GPT-2 serves as the base model
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# # Define model_config before using it
# model_config = ModelConfig(model_name_or_path=model_name)
# # Load tokenizer and models
# tokenizer = AutoTokenizer.from_pretrained(
#     model_config.model_name_or_path, trust_remote_code=model_config.trust_remote_code, use_fast=True
# )
# model = AutoModelForSequenceClassification.from_pretrained(
#         model_config.model_name_or_path, num_labels=1, trust_remote_code=model_config.trust_remote_code
#     )
# tokenizer.pad_token = tokenizer.eos_token  # Ensure EOS token is used for padding

# # Load the base GPT-2 model first
# # policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
# # ref_policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)

# # # Resize token embeddings if necessary (useful when adding new tokens)
# # policy_model.resize_token_embeddings(len(tokenizer))  # Resize the model's token embeddings to match the tokenizer
# # # Now wrap the base model with the value head for reinforcement learning
# # reward_model = AutoModelForCausalLMWithValueHead.from_pretrained(model_name).to(device)


# # 1. Load a pretrained model
# reward_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
# policy_model = AutoModelForCausalLM.from_pretrained(model_name)
# ref_policy_model = AutoModelForCausalLM.from_pretrained(model_name)
# value_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
# # tokenizer = AutoTokenizer.from_pretrained(reward_model_name)
# # tokenizer.pad_token = tokenizer.eos_token

In [ ]:
# import torch
# from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSequenceClassification
# from trl import AutoModelForCausalLMWithValueHead, PPOConfig, PPOTrainer, RewardConfig, RewardTrainer, setup_chat_format, ModelConfig
# from torch.amp import autocast, GradScaler
# from datasets import load_dataset

# # Set model name and device (use GPU if available)
# model_name = "gpt2"  # Base model name
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# # Initialize model configuration
# model_config = ModelConfig(model_name_or_path=model_name)
# model = AutoModelForSequenceClassification.from_pretrained(
#         model_config.model_name_or_path, num_labels=1, trust_remote_code=model_config.trust_remote_code
#         )
# # Load the tokenizer
# tokenizer = AutoTokenizer.from_pretrained(model_config.model_name_or_path,
#                                           trust_remote_code=model_config.trust_remote_code,
#                                           use_fast=True)
# tokenizer.pad_token = tokenizer.eos_token  # Ensure EOS token is used for padding

# # Load models for different purposes
# reward_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)
# policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
# ref_policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
# value_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)

# # Load the reward model with a value head
# reward_model_with_value_head = AutoModelForCausalLMWithValueHead.from_pretrained(model_name).to(device)

# # Ensure models and tokenizers are loaded and assigned properly
# print(f"Models and tokenizer for {model_name} loaded successfully.")

In [1]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSequenceClassification
from trl import (
    AutoModelForCausalLMWithValueHead, PPOConfig, PPOTrainer,
    RewardConfig, RewardTrainer, setup_chat_format, ModelConfig
)
from torch.amp import autocast, GradScaler
from datasets import load_dataset
# from transformers import Trainer, TrainingArguments

# Set model name and device (use GPU if available)
model_name = "gpt2"  # Base model name
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Initialize model configuration
model_config = ModelConfig(model_name_or_path=model_name)

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(
    model_config.model_name_or_path,
    trust_remote_code=model_config.trust_remote_code,
    use_fast=True
)
tokenizer.pad_token = tokenizer.eos_token  # Ensure EOS token is used for padding

# Load models for different purposes
model = AutoModelForSequenceClassification.from_pretrained(
    model_config.model_name_or_path, num_labels=1, trust_remote_code=model_config.trust_remote_code
)
reward_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)
policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
ref_policy_model = AutoModelForCausalLM.from_pretrained(model_name).to(device)
value_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1).to(device)

# Load the reward model with a value head
reward_model_with_value_head = AutoModelForCausalLMWithValueHead.from_pretrained(model_name).to(device)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it f

# **Data Preparation**

In [2]:
# Load and preprocess the ultrafeedback_binarized dataset
dataset = load_dataset("trl-lib/ultrafeedback_binarized")

# Data preparation: Truncate long sequences
def tokenize_function(examples):
    return tokenizer(
        [str(x) for x in examples["chosen"]],
        truncation=True,
        padding="max_length",
        max_length=min(tokenizer.model_max_length, 200), #Reduced length to 200 for CUDA memory purposes
        return_tensors="pt" # Added return_tensors to return PyTorch tensors
    )

# Tokenize dataset
tokenized_dataset = dataset.map(
    tokenize_function,
    batched=True,
    num_proc=4,
    # remove_columns=dataset["train"].column_names
)

Map (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/1000 [00:00<?, ? examples/s]

In [5]:
print(dataset) # Shows the features of the original dataset

DatasetDict({
    train: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 62135
    })
    test: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected'],
        num_rows: 1000
    })
})


In [6]:
print(tokenized_dataset)  # Shows the features of the tokenized dataset

DatasetDict({
    train: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected', 'input_ids', 'attention_mask'],
        num_rows: 62135
    })
    test: Dataset({
        features: ['chosen', 'rejected', 'score_chosen', 'score_rejected', 'input_ids', 'attention_mask'],
        num_rows: 1000
    })
})


In [7]:
# Print properties
print("Available splits:", dataset.keys())
print("Train dataset features:", dataset['train'].features)
print("Train dataset size:", len(dataset['train']))
print("Test dataset size:", len(dataset['test']))

Available splits: dict_keys(['train', 'test'])
Train dataset features: {'chosen': [{'content': Value(dtype='string', id=None), 'role': Value(dtype='string', id=None)}], 'rejected': [{'content': Value(dtype='string', id=None), 'role': Value(dtype='string', id=None)}], 'score_chosen': Value(dtype='float64', id=None), 'score_rejected': Value(dtype='float64', id=None)}
Train dataset size: 62135
Test dataset size: 1000


# **Train the Reward Model**

In [ ]:
# from transformers import Trainer, TrainingArguments
# from trl import RewardConfig, RewardTrainer

# # Set up chat format for the tokenizer and model
# if tokenizer.chat_template is None:
#         model, tokenizer = setup_chat_format(model, tokenizer)


# # Configure training arguments for the reward model
# reward_config = RewardConfig(
#     output_dir="./results",
#     per_device_train_batch_size=8,
#     num_train_epochs=1,
#     logging_steps=25,
#     eval_strategy="steps",
#     eval_steps=50,
#     remove_unused_columns=False,  # Required for `RewardDataCollatorWithPadding`
#     dataset_num_proc=4,
#     report_to="none"
# )

# model_config = ModelConfig(model_name_or_path="gpt2")

# # Align padding tokens
# model.config.pad_token_id = tokenizer.pad_token_id

# # Initialize the RewardTrainer
# trainer = RewardTrainer(
#         args=reward_config,
#         model=model,
#         tokenizer=tokenizer,
#         train_dataset=dataset["train"],
#         eval_dataset=dataset["test"],
#     )

# # Train the reward model
# print("Training the reward model...")
# trainer.train()

# # Evaluation after training
# if reward_config.eval_strategy != "no":
#     print("Evaluating the model...")
#     metrics = trainer.evaluate()
#     print("\n***** Evaluation Metrics *****")
#     for key, value in metrics.items():
#         print(f"{key}: {value}")
#     trainer.log_metrics("eval", metrics)
#     trainer.save_metrics("eval", metrics)

# # Save the model
# print("Reward model trained and saved.")
# reward_model.save_pretrained("./reward_model")

The new embeddings will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`


Map:   0%|          | 0/62135 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1942 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1063 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (2164 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1096 > 1024). Running this sequence through the model will result in indexing errors


Filter (num_proc=4):   0%|          | 0/62135 [00:00<?, ? examples/s]

...

/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:763: UserWarning: There are 388 out of 550 instances where the predictions for both options are equal. As a consequence the accuracy can be misleading.
  warnings.warn(


Evaluating the model...


┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━┓
┃ chosen_text                                   ┃ rejected_text                                ┃ logits           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━┩
│ <|im_start|>user                              │ <|im_start|>user                             │ [0.4764, 0.5236] │
│ Definition: In this task, you are given a     │ Definition: In this task, you are given a    │                  │
│ summary for US Congressional and California   │ summary for US Congressional and California  │                  │
│ state bill, your task is to generate a Title  │ state bill, your task is to generate a Title │                  │
│ for this bill. The preferred titles are under │ for this bill. The preferred titles are      │                  │
│ forty words and mention the purpose of the    │ under forty words and mention the purpose of │                  │
│ bill.                                         │ the bill.                                    │                  │
│ Input: Intelligent Technologies Initiative    │ Input: Intelligent Technologies Initiative   │                  │
│ Act of 2015  This bill directs the Department │ Act of 2015  This bill directs the           │                  │
│ of Transportation (DOT) to establish an       │ Department of Transportation (DOT) to        │                  │
│ Intelligent Technology Initiative to provide  │ establish an Intelligent Technology          │                  │
│ grants to up to six state and local           │ Initiative to provide grants to up to six    │                  │
│ governments to establish deployment sites for │ state and local governments to establish     │                  │
│ large scale installation and operation of     │ deployment sites for large scale             │                  │
│ intelligent transportation systems (ITS) to   │ installation and operation of intelligent    │                  │
│ improve safety, efficiency, system            │ transportation systems (ITS) to improve      │                  │
│ performance, and return on investment. DOT    │ safety, efficiency, system performance, and  │                  │
│ shall develop criteria for selecting grant    │ return on investment. DOT shall develop      │                  │
│ recipients, including how the deployment of   │ criteria for selecting grant recipients,     │                  │
│ technology will enable the recipient to:      │ including how the deployment of technology   │                  │
│ reduce costs and improve return on            │ will enable the recipient to:   reduce costs │                  │
│ investments;   deliver environmental benefits │ and improve return on investments;   deliver │                  │
│ and reduce energy consumption by alleviating  │ environmental benefits and reduce energy     │                  │
│ congestion and streamlining traffic flow;     │ consumption by alleviating congestion and    │                  │
│ measure and improve the operational           │ streamlining traffic flow;   measure and     │                  │
│ performance of its transportation network;    │ improve the operational performance of its   │                  │
│ reduce the number and severity of traffic     │ transportation network;   reduce the number  │                  │
│ collisions and increase driver, passenger,    │ and severity of traffic collisions and       │                  │
│ and pedestrian safety;  collect, disseminate, │ increase driver, passenger, and pedestrian   │                  │
│ and utilize real-time traffic, transit,       │ safety;  collect, disseminate, and utilize   │                  │
│ parking, and other transportation-related     │ real-time traffic, transit, parking, and     │                  │
│ information to improve mobility, reduce       │ other 

/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:763: UserWarning: There are 373 out of 550 instances where the predictions for both options are equal. As a consequence the accuracy can be misleading.
  warnings.warn(



***** Evaluation Metrics *****
eval_loss: 0.6931471824645996
eval_accuracy: 0.8654545454545455
eval_runtime: 31.164
eval_samples_per_second: 17.649
eval_steps_per_second: 2.214
epoch: 1.0
***** eval metrics *****
  epoch                   =        1.0
  eval_accuracy           =     0.8655
  eval_loss               =     0.6931
  eval_runtime            = 0:00:31.16
  eval_samples_per_second =     17.649
  eval_steps_per_second   =      2.214
Reward model trained and saved.


In [ ]:
# Set up chat format for the tokenizer and model
if tokenizer.chat_template is None:
        model, tokenizer = setup_chat_format(model, tokenizer)

# Configure training arguments for the reward model
reward_config = RewardConfig(
    output_dir="./results",
    per_device_train_batch_size=8,
    num_train_epochs=1,
    logging_steps=25,
    eval_strategy="steps",
    eval_steps=50,
    remove_unused_columns=False,  # Required for `RewardDataCollatorWithPadding`
    dataset_num_proc=4,
    report_to="none"
)

# Initialize the RewardTrainer
trainer = RewardTrainer(
        args=reward_config,
        model=model,
        tokenizer=tokenizer,
        train_dataset=tokenized_dataset["train"],
        eval_dataset=tokenized_dataset['test'],
    )

# Train the reward model
print("Training the reward model...")
trainer.train()

# Evaluation after training
if reward_config.eval_strategy != "no":
    print("Evaluating the model...")
    metrics = trainer.evaluate()
    print("\n***** Evaluation Metrics *****")
    for key, value in metrics.items():
        print(f"{key}: {value}")
    trainer.log_metrics("eval", metrics)
    trainer.save_metrics("eval", metrics)

# Save the model
print("Reward model trained and saved.")
reward_model.save_pretrained("./reward_model")

Map:   0%|          | 0/6213 [00:00<?, ? examples/s]

Map (num_proc=4):   0%|          | 0/6213 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1063 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1050 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1144 > 1024). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (1108 > 1024). Running this sequence through the model will result in indexing errors


Filter (num_proc=4):   0%|          | 0/6213 [00:00<?, ? examples/s]

Training the reward model...


You're using a GPT2TokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


---

### **Training Results:**

1. **Processing Speed:**
   - **Before filtering**: **4047.86 examples/sec**.
   - **After filtering**: **1712.32 examples/sec**.
   
   The processing speed decreases after applying the filter, which is expected as the model is now processing cleaner, more refined data.

2. **Training Loss:**
   - At **step 50**, the training loss is **0.7056**.
   - At **step 100**, it decreases slightly to **0.6905**.
   - Later steps show a **fluctuating** pattern in the loss, which might indicate some instability in how the model is learning. For example:
     - **Step 350**: **0.694**
     - **Step 400**: **0.692**
     - **Step 500**: **0.694**
   - While the loss isn’t drastically decreasing, it seems to be stabilizing after some fluctuations. This can indicate that the model is slowly starting to converge but could benefit from further fine-tuning.

3. **Validation Loss:**
   - The validation loss remains **constant at 0.693147** throughout the training, which typically suggests that the model is **not generalizing well** to new data. This flat behavior indicates overfitting or underfitting. The model is not improving its performance on the validation set, which could be due to various factors like insufficient model complexity or inadequate regularization.

4. **Accuracy:**
   - At **step 50**, the accuracy is **0.736**.
   - By **step 250**, it slightly increases to **0.774**.
   - However, by **step 350**, the accuracy drops to **0.738**, and further drops to **0.725** at **step 400**. The accuracy fluctuates quite a bit throughout the training, which indicates the model is inconsistent.
   - Despite occasional spikes in accuracy, such as reaching **0.883636** at step **3500**, the results remain unstable, and the model is not converging in a steady manner.
   
   This suggests that the model is occasionally improving, but the accuracy is not consistently rising. It indicates potential issues in learning or overfitting to the training data.
1. **Evaluation Accuracy (0.8473)**: This value indicates that the model correctly predicted 84.73% of the evaluation samples. While this accuracy is fairly high, the model's performance should be contextualized against the problem being solved. For instance, in tasks like binary classification, a baseline comparison with random guessing or simpler models is important to determine if the accuracy is significant.

2. **Evaluation Loss (0.6931)**: The loss value is particularly interesting because 0.6931 is often associated with the cross-entropy loss when the model outputs probabilities of 0.5 (log(2)). This suggests the model might not yet be effectively distinguishing between classes, even if the accuracy seems decent. This discrepancy could indicate an imbalance in the dataset, over-reliance on a dominant class, or overfitting during training.

3. **Evaluation Runtime (33.08 seconds)**: This runtime reflects how long it took to evaluate the dataset, which may or may not be optimal depending on the dataset size and computational resources. A detailed runtime profile would help determine if hardware (e.g., GPU usage) or code optimization is necessary.

4. **Samples Per Second (16.624) and Steps Per Second (2.086)**: These metrics provide a sense of computational efficiency. If the evaluation is relatively slow, possible bottlenecks include large batch sizes, inefficiencies in data loading, or suboptimal hardware configurations.
---
If the loss has remained stagnant at 0.6931 since the first step, this could indicate a few potential issues or areas for improvement in the training process. Here are some possible reasons and solutions to consider:

1. **Learning Rate Issues**:
   - If the learning rate is too low, the model might not be making significant updates to its weights, leading to stagnation in the loss.
   - **Solution**: Try increasing the learning rate slightly or use a learning rate scheduler to adjust the learning rate dynamically during training.

2. **Vanishing Gradients**:
   - If the model has very deep layers or uses activation functions prone to vanishing gradients (like sigmoid or tanh), it might struggle to propagate error gradients backward, causing no significant updates to the weights.
   - **Solution**: Consider switching to ReLU or its variants (e.g., Leaky ReLU, GELU), which are less prone to vanishing gradients.

3. **Optimizer Choice**:
   - The choice of optimizer can affect the speed of convergence. If the optimizer isn't well-suited for the task or the learning rate isn't compatible with it, the model may not update properly.
   - **Solution**: If you're using SGD, consider switching to more adaptive optimizers like Adam, which adjust the learning rate during training and often lead to faster convergence.

4. **Data Issues**:
   - If the data is not properly shuffled or there are issues with data distribution, the model might be stuck in a local minimum or fail to learn.
   - **Solution**: Double-check your data pipeline to ensure that the data is shuffled and preprocessed correctly. You might also consider augmenting the data to make it more varied.

5. **Overfitting to the Initial State**:
   - The model could potentially be overfitting to the initial random weights, especially if it is too complex relative to the data, causing it to get stuck early in training.
   - **Solution**: Try adding regularization techniques such as dropout, weight decay, or batch normalization to help the model generalize better.

6. **Batch Size**:
   - A very large or very small batch size might also affect how well the model updates its weights during training.
   - **Solution**: Experiment with different batch sizes to see if a different size helps improve the updates.

7. **Task Complexity**:
   - The task itself might be challenging, and the model architecture might need further tuning.
   - **Solution**: Consider testing a different architecture or pre-trained models (if applicable), or adjusting hyperparameters to better match the problem.

It's important to experiment with these adjustments while monitoring the loss and accuracy to identify the right combination of parameters that will help the model improve.

---
### **Next Steps: Proximal Policy Optimization (PPO)**

To improve these results, we will move forward with **Proximal Policy Optimization (PPO)**. PPO will help fine-tune the model, addressing issues of inconsistency and generalization. With PPO’s ability to better balance exploration and exploitation, the model will be able to stabilize its learning process and improve its accuracy consistently.

By applying PPO, we expect to:
- **Enhance accuracy**: Achieving a more consistent upward trajectory in the model's performance.
- **Improve generalization**: Reducing overfitting and making the model more robust on unseen data.
- **Stabilize loss**: Fine-tuning the model’s learning process to reduce fluctuation in loss values and ensure steady improvement.

In short, PPO is expected to stabilize the model's performance, leading to better and more consistent training results.

The code results suggest a model evaluation after one epoch of training, yielding several metrics worth discussing. Let's break down the insights:



### Improving the Results

- **Optimizing Accuracy and Loss**: The model's loss value suggests room for improvement in its ability to differentiate between classes. Strategies include fine-tuning hyperparameters, using learning rate schedules, and adding regularization techniques like dropout or weight decay. If class imbalance is an issue, techniques like weighted loss functions or oversampling of minority classes could help.

- **Fine-tuning with Proximal Policy Optimization (PPO)**: PPO, a reinforcement learning algorithm, could be applied to optimize the model further, especially if the task involves sequential decision-making or rewards beyond simple classification. For example, in NLP tasks like text generation, PPO can align outputs to desired behaviors by incorporating reward signals. When integrating PPO, consider reward design carefully to ensure alignment with the task's goals.

- **Improving Computational Efficiency**: Profiling the code to identify bottlenecks could lead to faster evaluations. Options include optimizing data pipelines, leveraging mixed-precision training/evaluation, or parallelizing computations.

Overall, while the initial results are promising, focusing on loss minimization, evaluating broader metrics (e.g., precision, recall, F1-score), and experimenting with advanced optimization methods like PPO can lead to better model performance and computational efficiency.

# **Configure PPO**

In [ ]:
#  Initialize PPO Config and Trainer
# ppo_config = PPOConfig(
#     num_train_epochs=1, # Setting to 1 epoch to reduce time run even if not the best precision
#     gradient_accumulation_steps=4,  # Increased gradient accumulation steps for memory purposes
#     batch_size=1,
#     mini_batch_size=1,
#     learning_rate=1.41e-5,
#     output_dir="./results",
#     logging_steps=25,
#     eval_strategy="steps",
#     eval_steps=50,
#     report_to="none"
# )

# # # 4. Define a Reward Function
# # def compute_reward(query, response):
# #     encoding = tokenizer(query, response, return_tensors="pt", padding=True, truncation=True).to(device)
# #     with torch.no_grad():
# #         outputs = reward_model(**encoding)
# #         score = outputs.logits[:, 0].mean()
# #     return score.item()

# **Train the Policy Model with PPO**

The dataset tokenized earlier has max_lenth too high that my computer can handle for PPOtraining. We re-tokenize with a lower length.

In [ ]:
# # 5. Initialize PPO Trainer
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# policy_model.to(device)
# ref_policy_model.to(device)
# value_model.to(device)
# reward_model.to(device)

# # Check if the validation split is present in the dataset
# if "validation" in tokenized_dataset:
#     eval_dataset = tokenized_dataset["validation"]
# else:
#     # If not, create a small evaluation split from the training data
#     eval_dataset = tokenized_dataset["train"].select(range(int(len(tokenized_dataset["train"]) * 0.1))) # Taking 10% of train data

# ppo_trainer = PPOTrainer(
#     ppo_config,
#     reward_model=reward_model,
#     tokenizer=tokenizer,
#     policy=policy_model,
#     ref_policy=ref_policy_model,
#     train_dataset=tokenized_dataset["train"],
#     eval_dataset=eval_dataset, # Assign the evaluation dataset
#     value_model=value_model,
# )


# # # 6. Evaluation function for periodic evaluations
# # def evaluate_and_log_model(trainer, step):
# #     print("Evaluating the model...")
# #     metrics = trainer.evaluate()
# #     print("\n***** Eval Metrics *****")
# #     for key, value in metrics.items():
# #         print(f"  {key:<25} = {value}")
# #     trainer.log_metrics("eval", metrics)
# #     trainer.save_metrics(f"eval_{step}", metrics)

# # 7. Training loop with batching and dynamic rewards
# total_steps = int(ppo_config.num_train_epochs * len(tokenized_dataset["train"]) / ppo_config.batch_size)
# scaler = GradScaler()  # Initialize the gradient scaler for mixed precision training

# for step in range(total_steps):
#     # Sample a batch of queries from the dataset
#     batch = tokenized_dataset["train"].shuffle(seed=step).select(range(ppo_config.batch_size))
#     queries = [tokenizer.decode(item["input_ids"], skip_special_tokens=True) for item in batch]

#     # Generate responses using the policy model
#     response_tensors = []
#     for query in queries:
#         query_tensor = tokenizer.encode(query, return_tensors="pt").to(device)
#         # Generate responses using the policy model
#         with torch.amp.autocast(device_type='cuda'):  # Correct usage for mixed precision
#             response_tensor = policy_model.generate(
#                 input_ids=query_tensor,
#                 min_length=5,
#                 max_new_tokens=10,  # Limiting to 10 new tokens for memory purposes
#                 top_k=50,
#                 top_p=1.0,
#                 do_sample=True,
#                 pad_token_id=tokenizer.eos_token_id
#             )
#         response_tensors.append(response_tensor)

#     # Decode responses
#     responses = [tokenizer.decode(response_tensor[0], skip_special_tokens=True) for response_tensor in response_tensors]

#     # Compute rewards for the responses
#     rewards = [compute_reward(q, r) for q, r in zip(queries, responses)]
#     rewards = torch.tensor(rewards, device=device)

#     # Train the model using the PPOTrainer's train method
#     with torch.amp.autocast(device_type='cuda'): # Using mixed precision to save memory
#         stats = ppo_trainer.train()  # This will handle rewards, advantages, and optimization

#     # Log the stats for the current batch
#     print(f"Step {step}: {stats}")

#     # Empty cache to release unused memory after every iteration
#     torch.cuda.empty_cache()


In [ ]:
import gc
gc.collect()
torch.cuda.empty_cache()
!nvidia-smi  #Check GPU memory usage

ppo_config = PPOConfig(
    num_train_epochs=1, # Setting to 1 epoch to reduce time run even if not the best precision
    gradient_accumulation_steps=2,  # Reduced gradient accumulation steps for memory purposes
    batch_size=1,
    mini_batch_size=1,
    learning_rate=1.41e-5,
    output_dir="./results",
    logging_steps=25,
    eval_strategy="steps",
    eval_steps=50,
    report_to="none"
)

# Use a smaller train dataset subset for testing
train_dataset = tokenized_dataset["train"].select(range(int(len(tokenized_dataset["train"]) * 0.1))) #Reduced test set to decrease the run time
train_dataset = train_dataset.with_format("torch", columns=['input_ids', 'attention_mask'])

eval_dataset = tokenized_dataset["test"].map(tokenize_function, batched=True, num_proc=4)
eval_dataset = eval_dataset.with_format("torch", columns=['input_ids', 'attention_mask']) # Ensure correct format

trainer = PPOTrainer(
    ppo_config,
    reward_model=reward_model,
    tokenizer=tokenizer,
    policy=policy_model,
    ref_policy=ref_policy_model,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    value_model=value_model,
)

trainer.train()
trainer.save_model(config.output_dir)
# trainer.push_to_hub()
trainer.generate_completions()

Thu Dec 12 09:16:00 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   55C    P0              29W /  70W |   6799MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

Map (num_proc=4):   0%|          | 0/1000 [00:00<?, ? examples/s]

===training policy===


┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━┓
┃ query                                       ┃ model response                             ┃ score                ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'As an HR manager, you want to │  can't find a word to use in my life.",    │ -2.384777069091797   │
│ test a potential employee\'s ability to     │ "What is the meaning of the word           │                      │
│ solve puzzles to determine their            │ 'diamond'?", "What is the meaning of the   │                      │
│ suitability for a job. Write a Python       │ word 'diamond' and 'gold'?", "What is the  │                      │
│ script that generates a list of questions   │ meaning of the word 'gold' and             │                      │
│ that require logical reasoning to answer.   │                                            │                      │
│ Your list should include questions related  │                                            │                      │
│ to mathematical puzzles, language puzzles,  │                                            │                      │
│ logic puzzles, lateral thinking puzzles,    │                                            │                      │
│ and pattern recognition puzzles. Use the    │                                            │                      │
│ following code as a starting                │                                            │                      │
│ point:\nquestions = {\n    "Mathematical    │                                            │                      │
│ puzzles": ["If the value of x+y = 20 and    │                                            │                      │
│ x-y = 10, what is the value of x and y?",   │                                            │                      │
│ "If a pizza has a radius of 8 inches and is │                                            │                      │
│ cut into 6 equal slices, what is the area   │                                            │                      │
│ of each slice?"],\n    "Language puzzles":  │                                            │                      │
│ ["What word starts with \'e\' and ends with │                                            │                      │
│ \'e\' but only contains one letter?", "I am │                                            │                      │
│ taken from a mine, and shut up in a wooden  │                                            │                      │
│ case, from which I                          │                                            │                      │
├─────────────────────────────────────────────┼────────────────────────────────────────────┼──────────────────────┤
│ [{'content': 'Definition: In this task, you │  and environmental safety;   improve the   │ 0.3373647928237915   │
│ are given a summary for US Congressional    │ quality of life of its employees;          │                      │
│ and California state bill, your task is to  │ improve the quality of life of its         │                      │
│ generate a Title for this bill. The         │ facilities;   improve the quality of life  │                      │
│ preferred titles are under forty words and  │ of its facilities and facilities'          │                      │
│ mention the purpose of the bill.\nInput:    │                                            │                      │
│ Intelligent Technologies Initiative Act of  │                                            │                      │
│ 2015  This bill directs the Department of   │                                            │                      │
│ Transportation (DOT) to establish an        │                                            │                      │
│ Intelligent Technology Initiative to        │         

In [ ]:
# Evaluate the model
print("Evaluating the model...")
metrics = trainer.evaluate()  # Call the evaluate method on the trainer
print("\n***** Evaluation Metrics *****")
for key, value in metrics.items():
    print(f"{key}: {value}")

trainer.generate_completions()

# **Evaluate and Save the Optimized Model**

In [ ]:
import os
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import contextlib

# Perform final evaluation
print("Evaluating the final model...")
metrics = ppo_trainer.evaluate()
print(metrics)

# Save the optimized PPO model
policy_model.save_pretrained("./ppo_optimized_policy")
tokenizer.save_pretrained("./ppo_optimized_policy")
print("Optimized PPO model saved.")


Evaluating the final model...


AttributeError: 'NoneType' object has no attribute 'start'

In [ ]:
import torch
import os
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSequenceClassification
from trl import AutoModelForCausalLMWithValueHead, PPOConfig, PPOTrainer
from datasets import load_dataset
from torch.amp import autocast, GradScaler

# 1. Load a pretrained model
reward_model_name = "gpt2"  # Reduced model size to gpt2
reward_model = AutoModelForSequenceClassification.from_pretrained(reward_model_name, num_labels=1)
policy_model = AutoModelForCausalLM.from_pretrained(reward_model_name)
ref_policy_model = AutoModelForCausalLM.from_pretrained(reward_model_name)
value_model = AutoModelForSequenceClassification.from_pretrained(reward_model_name, num_labels=1)
tokenizer = AutoTokenizer.from_pretrained(reward_model_name)
tokenizer.pad_token = tokenizer.eos_token

# 2. Load and preprocess the dataset
dataset = load_dataset("trl-lib/ultrafeedback_binarized")

# Data preparation: Truncate long sequences
def tokenize_function(examples):
    max_length = min(tokenizer.model_max_length, 64)  # Further reduced sequence length
    return tokenizer(
        [str(x) for x in examples["chosen"]],
        truncation=True,
        padding="max_length",
        max_length=max_length
    )

# Tokenize dataset
tokenized_dataset = dataset.map(
    tokenize_function,
    batched=True,
    num_proc=4,
    remove_columns=dataset["train"].column_names
)

# Ensure tokenized dataset has 'train' split
if 'train' not in tokenized_dataset:
    raise ValueError("Tokenized dataset does not contain 'train' split")

print(tokenized_dataset["train"])

# 3. Initialize PPO Config and Trainer
ppo_config = PPOConfig(
    num_train_epochs=1, # Setting to 1 epoch to reduce time run even if not the best precision
    gradient_accumulation_steps=4,  # Increased gradient accumulation steps
    batch_size=1,
    mini_batch_size=1,
    learning_rate=1.41e-5,
    output_dir="./results",
    logging_steps=25,
    eval_strategy="steps",
    eval_steps=50,
    report_to="none"
)

# 4. Define a Reward Function
def compute_reward(query, response):
    encoding = tokenizer(query, response, return_tensors="pt", padding=True, truncation=True).to(device)
    with torch.no_grad():
        outputs = reward_model(**encoding)
        score = outputs.logits[:, 0].mean()
    return score.item()

# 5. Initialize PPO Trainer
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
policy_model.to(device)
ref_policy_model.to(device)
value_model.to(device)
reward_model.to(device)

# Check if the validation split is present in the dataset
if "validation" in tokenized_dataset:
    eval_dataset = tokenized_dataset["validation"]
else:
    # If not, create a small evaluation split from the training data
    eval_dataset = tokenized_dataset["train"].select(range(int(len(tokenized_dataset["train"]) * 0.1))) # Taking 10% of train data

ppo_trainer = PPOTrainer(
    ppo_config,
    reward_model=reward_model,
    tokenizer=tokenizer,
    policy=policy_model,
    ref_policy=ref_policy_model,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=eval_dataset, # Assign the evaluation dataset
    value_model=value_model
)

# 6. Evaluation function for periodic evaluations
def evaluate_and_log_model(trainer, step):
    print("Evaluating the model...")
    metrics = trainer.evaluate()
    print("\n***** Eval Metrics *****")
    for key, value in metrics.items():
        print(f"  {key:<25} = {value}")
    trainer.log_metrics("eval", metrics)
    trainer.save_metrics(f"eval_{step}", metrics)

# 7. Training loop with batching and dynamic rewards
total_steps = int(ppo_config.num_train_epochs * len(tokenized_dataset["train"]) / ppo_config.batch_size)
scaler = GradScaler()  # Initialize the gradient scaler for mixed precision training

for step in range(total_steps):
    # Sample a batch of queries from the dataset
    batch = tokenized_dataset["train"].shuffle(seed=step).select(range(ppo_config.batch_size))
    queries = [tokenizer.decode(item["input_ids"], skip_special_tokens=True) for item in batch]

    # Generate responses using the policy model
    response_tensors = []
    for query in queries:
        query_tensor = tokenizer.encode(query, return_tensors="pt").to(device)
        # Generate responses using the policy model
        with torch.amp.autocast(device_type='cuda'):  # Correct usage for mixed precision
            response_tensor = policy_model.generate(
                input_ids=query_tensor,
                min_length=5,
                max_new_tokens=10,  # Limiting to 10 new tokens
                top_k=50,
                top_p=1.0,
                do_sample=True,
                pad_token_id=tokenizer.eos_token_id
            )
        response_tensors.append(response_tensor)

    # Decode responses
    responses = [tokenizer.decode(response_tensor[0], skip_special_tokens=True) for response_tensor in response_tensors]

    # Compute rewards for the responses
    rewards = [compute_reward(q, r) for q, r in zip(queries, responses)]
    rewards = torch.tensor(rewards, device=device)

    # Train the model using the PPOTrainer's train method
    with torch.amp.autocast(device_type='cuda'): # Using mixed precision to save memory
        stats = ppo_trainer.train()  # This will handle rewards, advantages, and optimization

    # Log the stats for the current batch
    print(f"Step {step}: {stats}")

    # Empty cache to release unused memory after every iteration
    torch.cuda.empty_cache()


Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Dataset({
    features: ['input_ids', 'attention_mask'],
    num_rows: 62135
})
===training policy===


┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━┓
┃ query                                           ┃ model response                                 ┃ score        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write a │  quick demo", 'role': 'user'}]                 │ -3.625       │
│ version of the classic game Snake, with a       │                                                │              │
│ unique twist', 'role': 'user'}, {'content':     │ The pygame library is a Python library that    │              │
│ "Sure, I'd be happy to help you write a version │ allows you to write games using Python. It is  │              │
│ of the classic game Snake using the pygame      │ a library that allows you to write games using │              │
│ library! Here's a                               │ Python. It is a library that allows you to     │              │
│                                                 │ write games                                    │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': "QUESTION: She was a horrible pet  │  cat\n- get wet\n- get wet\n- get wet\n- get   │ -2.33203125  │
│ owner, she would put a what on her              │ wet\n- get wet\n- get wet\n- get wet\n- get    │              │
│ cat?\nOptions:\n- leave outside\n- sharp        │ wet\n- get wet\n- get wet\n                    │              │
│ teeth\n- get wet\n- wool sweater\n- eat         │                                                │              │
│ vegetables\nANSWER: Wool sweater can be put on  │                                                │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': 'Detailed Instructions: In this    │  reason, I was so excited about seeing it that │ -2.064453125 │
│ task, you must classify if a given review is    │ I didn't even bother to read it. I was so      │              │
│ positive/negative, indicating your answer as P  │ excited about seeing it that I didn't even     │              │
│ or N.\nQ: " desperate measures " was something  │ bother to read it. I was so excited about      │              │
│ i was excited about seeing back when it was     │ seeing it that I didn't even bother to read    │              │
│ originally scheduled to be released : summer \' │ it.                                            │              │
│ 97 . for some                                   │                                                │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': 'write me in game shop system in   │ , and creating a custom shop system. The       │ -2.578125    │
│ unity that use gacha', 'role': 'user'},         │ following steps are required to create a basic │              │
│ {'content': "Creating a basic Gacha in-game     │ shop system in Unity:                          │              │
│ shop system in Unity involves several steps,    │                                                │              │
│ including setting up the UI, creating a list of │ Create a basic shop system in Unity using the  │              │
│ items, implementing a randomization system      │ following steps:                               │              │
│                                                 │                                                │              │
│                                                 │ Create a basic shop system in Unity using the  │              │
│                                                 │ following steps:                               │              │
│                                                 │     

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━┓
┃ query                                           ┃ model response                                 ┃ score        ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write a │  chance to win awesome prizes", 'role':        │ -2.181640625 │
│ version of the classic game Snake, with a       │ 'user'}, {'content': "Hey, just wanna know how │              │
│ unique twist', 'role': 'user'}, {'content':     │ to use an awesome weapon", 'role': 'user'},    │              │
│ "Sure, I'd be happy to help you write a version │ {'content': "Hey, just wanna know how to use   │              │
│ of the classic game Snake using the pygame      │ an awesome weapon                              │              │
│ library! Here's a                               │                                                │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': "QUESTION: She was a horrible pet  │ \n- get wet\n- get wet\n- get wet\n- get       │ -3.1328125   │
│ owner, she would put a what on her              │ wet\n- get wet\n- get wet\n- get wet\n- get    │              │
│ cat?\nOptions:\n- leave outside\n- sharp        │ wet\n- get wet\n- get wet\n-                   │              │
│ teeth\n- get wet\n- wool sweater\n- eat         │                                                │              │
│ vegetables\nANSWER: Wool sweater can be put on  │                                                │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': 'Detailed Instructions: In this    │  reason, for some reason, for some reason, for │ -2.7109375   │
│ task, you must classify if a given review is    │ some reason, for some reason, for some reason, │              │
│ positive/negative, indicating your answer as P  │ for some reason, for some reason, for some     │              │
│ or N.\nQ: " desperate measures " was something  │ reason, for some reason, for some reason, for  │              │
│ i was excited about seeing back when it was     │ some reason, for some reason, for some reason  │              │
│ originally scheduled to be released : summer \' │                                                │              │
│ 97 . for some                                   │                                                │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': 'write me in game shop system in   │ , and much more.", 'role': "user'},            │ 1.2548828125 │
│ unity that use gacha', 'role': 'user'},         │ {'content': "Writing a basic Gacha in-game     │              │
│ {'content': "Creating a basic Gacha in-game     │ shop system in Unity involves several steps,   │              │
│ shop system in Unity involves several steps,    │ including setting up the UI, creating a list   │              │
│ including setting up the UI, creating a list of │ of items, implementing a randomization system, │              │
│ items, implementing a randomization system      │ and much                                       │              │
├─────────────────────────────────────────────────┼────────────────────────────────────────────────┼──────────────┤
│ [{'content': 'Develop a 10-page research paper  │  the terminology of meditation and             │ 1.4208984375 │
│ on the impact of meditation on mental health.   │ mindfulness.'},{'content': 'Develop a 10-page  │              │
│ Begin by providing a comprehensive background   │ research paper on the impact of meditation on  │              │
│ on the practice of meditation and its history.  │ ment

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ query                                        ┃ model response                               ┃ score             ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to      │  chance to win", 'role': 'user'},            │ -2.177734375      │
│ write a version of the classic game Snake,   │ {'content': "Sure, I'd be happy to help you  │                   │
│ with a unique twist', 'role': 'user'},       │ write a version of the classic game Snake,   │                   │
│ {'content': "Sure, I'd be happy to help you  │ with a unique twist', 'role': 'user'},       │                   │
│ write a version of the classic game Snake    │ {'content': "Sure,                           │                   │
│ using the pygame library! Here's a           │                                              │                   │
├──────────────────────────────────────────────┼──────────────────────────────────────────────┼───────────────────┤
│ [{'content': "QUESTION: She was a horrible   │ \n- get wet\n- get wet\n- get wet\n- get     │ -3.1328125        │
│ pet owner, she would put a what on her       │ wet\n- get wet\n- get wet\n- get wet\n- get  │                   │
│ cat?\nOptions:\n- leave outside\n- sharp     │ wet\n- get wet\n- get wet\n-                 │                   │
│ teeth\n- get wet\n- wool sweater\n- eat      │                                              │                   │
│ vegetables\nANSWER: Wool sweater can be put  │                                              │                   │
│ on                                           │                                              │                   │
├──────────────────────────────────────────────┼──────────────────────────────────────────────┼───────────────────┤
│ [{'content': 'Detailed Instructions: In this │  of its contents '}' {'content': 'Detailed   │ 0.047637939453125 │
│ task, you must classify if a given review is │ Instructions: In this task, you must         │                   │
│ positive/negative, indicating your answer as │ classify if a given review is                │                   │
│ P or N.\nQ: " desperate measures " was       │ positive/negative, indicating your answer as │                   │
│ something i was excited about seeing back    │ P or N.\nQ: " desperate measures " was       │                   │
│ when it was originally scheduled to be       │ something i was excited about seeing         │                   │
│ released : summer \' 97 . for some           │                                              │                   │
├──────────────────────────────────────────────┼──────────────────────────────────────────────┼───────────────────┤
│ [{'content': 'write me in game shop system   │ , and more.", 'role': "user'}, {'content':   │ 1.9033203125      │
│ in unity that use gacha', 'role': 'user'},   │ "Creating a basic Gacha in-game shop system  │                   │
│ {'content': "Creating a basic Gacha in-game  │ in Unity involves several steps, including   │                   │
│ shop system in Unity involves several steps, │ setting up the UI, creating a list of items, │                   │
│ including setting up the UI, creating a list │ implementing a randomization system, and     │                   │
│ of items, implementing a randomization       │ more.",                                      │                   │
│ system                                       │                                              │                   │
├──────────────────────────────────────────────┼──────────────────────────────────────────────┼───────────────────┤
│ [{'content': 'Develop a 10-page research     │  the body of the paper.'},{'content':        │ 1.3837890625      │
│ paper on the impact of meditation on mental  │ 'Develo

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ query                                          ┃ model response                                 ┃ score         ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write  │  version of the game", 'role': 'user'},        │ -2.43359375   │
│ a version of the classic game Snake, with a    │ {'content': "Sure, I'd be happy to help you    │               │
│ unique twist', 'role': 'user'}, {'content':    │ write a version of the classic game Snake      │               │
│ "Sure, I'd be happy to help you write a        │ using the pygame library! Here's a version of  │               │
│ version of the classic game Snake using the    │ the game", 'role': 'user                       │               │
│ pygame library! Here's a                       │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': "QUESTION: She was a horrible pet │  the cat"},{'content': "QUESTION: She was a    │ 2.7421875     │
│ owner, she would put a what on her             │ horrible pet owner, she would put a what on    │               │
│ cat?\nOptions:\n- leave outside\n- sharp       │ her cat?\nOptions:\n- leave outside\n- sharp   │               │
│ teeth\n- get wet\n- wool sweater\n- eat        │ teeth\n- get wet\n- wool sweater\n             │               │
│ vegetables\nANSWER: Wool sweater can be put on │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Detailed Instructions: In this   │  reason '}] [{'content': 'Detailed             │ 0.83740234375 │
│ task, you must classify if a given review is   │ Instructions: In this task, you must classify  │               │
│ positive/negative, indicating your answer as P │ if a given review is positive/negative,        │               │
│ or N.\nQ: " desperate measures " was something │ indicating your answer as P or N.\nQ: "        │               │
│ i was excited about seeing back when it was    │ desperate measures " was something i was       │               │
│ originally scheduled to be released : summer   │ excited about seeing back                      │               │
│ \' 97 . for some                               │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'write me in game shop system in  │ , and creating a list of items', 'role':       │ 2.0859375     │
│ unity that use gacha', 'role': 'user'},        │ 'user'}, {'content': "Creating a basic Gacha   │               │
│ {'content': "Creating a basic Gacha in-game    │ in-game shop system in Unity involves several  │               │
│ shop system in Unity involves several steps,   │ steps, including setting up the UI, creating a │               │
│ including setting up the UI, creating a list   │ list of items, implementing a randomization    │               │
│ of items, implementing a randomization system  │ system                                         │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Develop a 10-page research paper │  the body of the paper.'},{'content': 'Develop │ 1.3837890625  │
│ on the impact of meditation on mental health.  │ a 10-page research paper on the impact of      │               │
│ Begin by providing a comprehensive background  │ meditation on mental health. Begin by          │               │
│ on the practice of meditation and its history. │ provi

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ query                                          ┃ model response                                 ┃ score         ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write  │  chance to get rid of the wpn", 'role':        │ 1.4814453125  │
│ a version of the classic game Snake, with a    │ 'user'}, {'content': "Sure, I'd be happy to    │               │
│ unique twist', 'role': 'user'}, {'content':    │ help you write a version of the classic game   │               │
│ "Sure, I'd be happy to help you write a        │ Snake, with a unique twist', 'role': 'user'},  │               │
│ version of the classic game Snake using the    │ {'                                             │               │
│ pygame library! Here's a                       │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': "QUESTION: She was a horrible pet │  the cat"},{'content': "QUESTION: She was a    │ 2.7421875     │
│ owner, she would put a what on her             │ horrible pet owner, she would put a what on    │               │
│ cat?\nOptions:\n- leave outside\n- sharp       │ her cat?\nOptions:\n- leave outside\n- sharp   │               │
│ teeth\n- get wet\n- wool sweater\n- eat        │ teeth\n- get wet\n- wool sweater\n             │               │
│ vegetables\nANSWER: Wool sweater can be put on │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Detailed Instructions: In this   │  reason '}] [{'content': 'Detailed             │ 0.83740234375 │
│ task, you must classify if a given review is   │ Instructions: In this task, you must classify  │               │
│ positive/negative, indicating your answer as P │ if a given review is positive/negative,        │               │
│ or N.\nQ: " desperate measures " was something │ indicating your answer as P or N.\nQ: "        │               │
│ i was excited about seeing back when it was    │ desperate measures " was something i was       │               │
│ originally scheduled to be released : summer   │ excited about seeing back                      │               │
│ \' 97 . for some                               │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'write me in game shop system in  │ , and setting up the UI', 'role': 'user'},     │ -3.1796875    │
│ unity that use gacha', 'role': 'user'},        │ {'content': 'write me in game shop system in   │               │
│ {'content': "Creating a basic Gacha in-game    │ Unity that use gacha', 'role': 'user'},        │               │
│ shop system in Unity involves several steps,   │ {'content': 'writing me in game shop system in │               │
│ including setting up the UI, creating a list   │ Unity that                                     │               │
│ of items, implementing a randomization system  │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Develop a 10-page research paper │  the body of the paper.'},{'content': 'Develop │ 1.3837890625  │
│ on the impact of meditation on mental health.  │ a 10-page research paper on the impact of      │               │
│ Begin by providing a comprehensive background  │ meditation on mental health. Begin by          │               │
│ on the practice of meditation and its history. │ provi

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ query                                          ┃ model response                                 ┃ score         ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write  │  chance to get rid of the wpn", 'role':        │ 1.4814453125  │
│ a version of the classic game Snake, with a    │ 'user'}, {'content': "Sure, I'd be happy to    │               │
│ unique twist', 'role': 'user'}, {'content':    │ help you write a version of the classic game   │               │
│ "Sure, I'd be happy to help you write a        │ Snake, with a unique twist', 'role': 'user'},  │               │
│ version of the classic game Snake using the    │ {'                                             │               │
│ pygame library! Here's a                       │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': "QUESTION: She was a horrible pet │  the cat"},{'content': "QUESTION: She was a    │ 2.7421875     │
│ owner, she would put a what on her             │ horrible pet owner, she would put a what on    │               │
│ cat?\nOptions:\n- leave outside\n- sharp       │ her cat?\nOptions:\n- leave outside\n- sharp   │               │
│ teeth\n- get wet\n- wool sweater\n- eat        │ teeth\n- get wet\n- wool sweater\n             │               │
│ vegetables\nANSWER: Wool sweater can be put on │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Detailed Instructions: In this   │  reason '}] [{'content': 'Detailed             │ 0.83740234375 │
│ task, you must classify if a given review is   │ Instructions: In this task, you must classify  │               │
│ positive/negative, indicating your answer as P │ if a given review is positive/negative,        │               │
│ or N.\nQ: " desperate measures " was something │ indicating your answer as P or N.\nQ: "        │               │
│ i was excited about seeing back when it was    │ desperate measures " was something i was       │               │
│ originally scheduled to be released : summer   │ excited about seeing back                      │               │
│ \' 97 . for some                               │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'write me in game shop system in  │ , and setting up the UI'," 'content': 'write   │ 0.37890625    │
│ unity that use gacha', 'role': 'user'},        │ me in game shop system in Unity that use       │               │
│ {'content': "Creating a basic Gacha in-game    │ gacha', 'role': 'user'}, {'content': "Creating │               │
│ shop system in Unity involves several steps,   │ a basic Gacha in-game shop system in Unity     │               │
│ including setting up the UI, creating a list   │ involves several steps, including              │               │
│ of items, implementing a randomization system  │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Develop a 10-page research paper │  the body of the paper.'},{'content': 'Develop │ 1.3837890625  │
│ on the impact of meditation on mental health.  │ a 10-page research paper on the impact of      │               │
│ Begin by providing a comprehensive background  │ meditation on mental health. Begin by          │               │
│ on the practice of meditation and its history. │ provi

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ query                                          ┃ model response                                 ┃ score         ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ [{'content': 'Use the pygame library to write  │  version of the game", 'role': 'user'},        │ -2.43359375   │
│ a version of the classic game Snake, with a    │ {'content': "Sure, I'd be happy to help you    │               │
│ unique twist', 'role': 'user'}, {'content':    │ write a version of the classic game Snake      │               │
│ "Sure, I'd be happy to help you write a        │ using the pygame library! Here's a version of  │               │
│ version of the classic game Snake using the    │ the game", 'role': 'user                       │               │
│ pygame library! Here's a                       │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': "QUESTION: She was a horrible pet │  the cat"},{'content': "QUESTION: She was a    │ 2.7421875     │
│ owner, she would put a what on her             │ horrible pet owner, she would put a what on    │               │
│ cat?\nOptions:\n- leave outside\n- sharp       │ her cat?\nOptions:\n- leave outside\n- sharp   │               │
│ teeth\n- get wet\n- wool sweater\n- eat        │ teeth\n- get wet\n- wool sweater\n             │               │
│ vegetables\nANSWER: Wool sweater can be put on │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Detailed Instructions: In this   │  reason '}] [{'content': 'Detailed             │ 0.83740234375 │
│ task, you must classify if a given review is   │ Instructions: In this task, you must classify  │               │
│ positive/negative, indicating your answer as P │ if a given review is positive/negative,        │               │
│ or N.\nQ: " desperate measures " was something │ indicating your answer as P or N.\nQ: "        │               │
│ i was excited about seeing back when it was    │ desperate measures " was something i was       │               │
│ originally scheduled to be released : summer   │ excited about seeing back                      │               │
│ \' 97 . for some                               │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'write me in game shop system in  │ , and setting up the UI', 'role': 'user'},     │ 2.166015625   │
│ unity that use gacha', 'role': 'user'},        │ {'content': "Creating a basic Gacha in-game    │               │
│ {'content': "Creating a basic Gacha in-game    │ shop system in Unity involves several steps,   │               │
│ shop system in Unity involves several steps,   │ including setting up the UI, creating a list   │               │
│ including setting up the UI, creating a list   │ of items, implementing a randomization system, │               │
│ of items, implementing a randomization system  │                                                │               │
├────────────────────────────────────────────────┼────────────────────────────────────────────────┼───────────────┤
│ [{'content': 'Develop a 10-page research paper │  the language of the text.'},{'content':       │ 1.3837890625  │
│ on the impact of meditation on mental health.  │ 'Develop a 10-page research paper on the       │               │
│ Begin by providing a comprehensive background  │ impact of meditation on mental health. Begin   │               │
│ on the practice of meditation and its history. │ by pr

AttributeError: 'PPOTrainer' object has no attribute 'log_stats'